<a href="https://colab.research.google.com/github/jmhuer/shift_invariant_dictionary_learning/blob/main/dictionarylearning_midipiano.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Set up enviroment


###Setup Environment and Dependencies. Check GPU.

In [1]:
#@title Check if GPU (driver) is avaiiable (you do not want to run this on CPU, trust me)
!nvcc --version
!nvidia-smi

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2020 NVIDIA Corporation
Built on Wed_Jul_22_19:09:09_PDT_2020
Cuda compilation tools, release 11.0, V11.0.221
Build cuda_11.0_bu.TC445_37.28845127_0
Sun Jul 11 06:12:57 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 470.42.01    Driver Version: 460.32.03    CUDA Version: 11.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   43C    P0    27W / 250W |      0MiB / 16280MiB |      0%      Default |
|                               |         

In [2]:
#@title Clone/Install all dependencies
!git clone https://github.com/asigalov61/midi-neural-processor
!git clone https://github.com/asigalov61/MusicTransformer-Pytorch
!pip install tqdm
!pip install progress
!pip install pretty-midi
!pip install pypianoroll
!pip install matplotlib
!pip install librosa
!pip install scipy
!pip install pillow
!apt install fluidsynth #Pip does not work for some reason. Only apt works
!pip install midi2audio
!pip install mir_eval
!cp /usr/share/sounds/sf2/FluidR3_GM.sf2 /content/font.sf2

Cloning into 'midi-neural-processor'...
remote: Enumerating objects: 26, done.
remote: Total 26 (delta 0), reused 0 (delta 0), pack-reused 26
Unpacking objects: 100% (26/26), done.
Cloning into 'MusicTransformer-Pytorch'...
remote: Enumerating objects: 385, done.
remote: Total 385 (delta 0), reused 0 (delta 0), pack-reused 385
Receiving objects: 100% (385/385), 101.10 KiB | 5.05 MiB/s, done.
Resolving deltas: 100% (207/207), done.
  Created wheel for progress: filename=progress-1.5-cp37-none-any.whl size=8088 sha256=dff86c47df89fae048998c439492eebae0b03f7aa2f1755342c0c73c981a6f8c
  Stored in directory: /root/.cache/pip/wheels/6c/c8/80/32a294e3041f006c661838c05a411c7b7ffc60ff939d14e116
Successfully built progress
     |████████████████████████████████| 5.6MB 7.2MB/s 
     |████████████████████████████████| 51kB 6.3MB/s 
  Created wheel for pretty-midi: filename=pretty_midi-0.2.9-cp37-none-any.whl size=5591958 sha256=68fb89a9b7b11db0bd48206d6ab47ff51f535a82f9c93dce5b721d52528ae7b5
  Stor

In [3]:
#@title Import all needed modules
import numpy as np
import pickle
import os
import sys
import math
import random
# For plotting
import pypianoroll
from pypianoroll import Multitrack, Track
import matplotlib
import matplotlib.pyplot as plt
#matplotlib.use('SVG')
#%matplotlib inline
#matplotlib.get_backend()
import mir_eval.display
import librosa
import librosa.display
# For rendering output audio
import pretty_midi
from midi2audio import FluidSynth
from google.colab import output
from IPython.display import display, Javascript, HTML, Audio

#Option 1: MAESTRO DataSet

In [4]:
#@title Download Google Magenta MAESTRO v.2.0.0 Piano MIDI Dataset (~1300 MIDIs)
%cd /content/MusicTransformer-Pytorch/dataset/
!wget 'https://storage.googleapis.com/magentadata/datasets/maestro/v2.0.0/maestro-v2.0.0-midi.zip'
!unzip maestro-v2.0.0-midi.zip
%cd /content/MusicTransformer-Pytorch/

/content/MusicTransformer-Pytorch/dataset
--2021-07-11 06:13:55--  https://storage.googleapis.com/magentadata/datasets/maestro/v2.0.0/maestro-v2.0.0-midi.zip
Resolving storage.googleapis.com (storage.googleapis.com)... 173.194.203.128, 74.125.199.128, 74.125.20.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|173.194.203.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 59243107 (56M) [application/zip]
Saving to: ‘maestro-v2.0.0-midi.zip’

maestro-v2.0.0-midi 100%[===================>]  56.50M  73.5MB/s    in 0.8s    

2021-07-11 06:13:56 (73.5 MB/s) - ‘maestro-v2.0.0-midi.zip’ saved [59243107/59243107]

Archive:  maestro-v2.0.0-midi.zip
   creating: maestro-v2.0.0/
  inflating: maestro-v2.0.0/maestro-v2.0.0.csv  
   creating: maestro-v2.0.0/2008/
  inflating: maestro-v2.0.0/2008/MIDI-Unprocessed_13_R1_2008_01-04_ORIG_MID--AUDIO_13_R1_2008_wav--1.midi  
  inflating: maestro-v2.0.0/2008/MIDI-Unprocessed_03_R1_2008_01-04_ORIG_MID--AUDIO_0

In [5]:
#@title Prepare directory sctructure and MIDI processor
%cd /content/
!mv midi-neural-processor midi_processor
%cd /content/MusicTransformer-Pytorch/

/content
/content/MusicTransformer-Pytorch


In [6]:
#@title Process MAESTRO MIDI DataSet
!python3 preprocess_midi.py '/content/MusicTransformer-Pytorch/dataset/maestro-v2.0.0'

Preprocessing midi files and saving to ./dataset/e_piano
Found 1282 pieces
Preprocessing...
50 / 1282
100 / 1282
Num Train: 93
Num Val: 18
Num Test: 20
Done!



In [21]:
from processor import encode_midi, decode_midi

                  
from dataset.e_piano import create_epiano_datasets, compute_epiano_accuracy


train_dataset, val_dataset, test_dataset = create_epiano_datasets("/content/MusicTransformer-Pytorch/dataset/e_piano", 2048)

print(list(train_dataset)[0][0].numpy())
print(len(list(train_dataset)[9][0]))
# tmp = []
# name = "test111"
# for point in train_dataset:
#     # isthis = decode_midi(point[0].numpy(), name + ".mid")
#     isthis = decode_midi(point[0].numpy())
#     tmp.append(isthis.estimate_tempo())


print("tempo:" , tmp )

decode_midi(list(train_dataset)[80][0].numpy(), name + ".mid")
FluidSynth("/content/font.sf2").midi_to_audio(name + ".mid", name + ".wav")
Audio(name + ".wav")


[265 211 370 ... 378  68 262]
2048
info removed pitch: 71
info removed pitch: 77
info removed pitch: 72
info removed pitch: 65
info removed pitch: 62
info removed pitch: 69
info removed pitch: 74
info removed pitch: 70
info removed pitch: 63
info removed pitch: 68
info removed pitch: 75
info removed pitch: 67
info removed pitch: 66
info removed pitch: 59
info removed pitch: 79
info removed pitch: 73
info removed pitch: 78
info removed pitch: 85
info removed pitch: 91
info removed pitch: 83
info removed pitch: 89
info removed pitch: 86
info removed pitch: 80
info removed pitch: 87
info removed pitch: 84
info removed pitch: 82
info removed pitch: 81
info removed pitch: 54
info removed pitch: 55
info removed pitch: 43
info removed pitch: 56
info removed pitch: 44
info removed pitch: 89
info removed pitch: 62
info removed pitch: 59
info removed pitch: 98
info removed pitch: 86
info removed pitch: 57
info removed pitch: 97
info removed pitch: 49
info removed pitch: 97
info removed pitch: 61

#Train the Model